# From Landmarks to Animations

### Víctor Ubieto, 2022

### victoremilio.ubieto@upf.edu | victor.ubieto@e-campus.uab.cat

In [ ]:
import os
import math
import json
import shutil
import random
import numpy as np
import tensorflow as tf
import tensorflowjs as tfjs
import matplotlib.pyplot as plt
from itertools import zip_longest
from scipy.signal import savgol_filter
from tensorflow.keras import layers, optimizers
from tensorflow.keras.models import Sequential, load_model

physical_device = tf.config.experimental.list_physical_devices('GPU')
print(f'Device found : {physical_device}')
tf.config.experimental.set_memory_growth(physical_device[0], True)


### Load the input and output data from the dataset. Also performs data augmentation.
**project_path:** Path to the project folder.
**dataset_dir:** Path to the dataset folder.
**flag_mirror:** True if you want to load also the mirrored animations (data augmentation).
**flag_transformations:** True if you want to apply transformations (zoom and movement) to the animations (data augmentation).
**ratio_transformations:** Number between 0 and 1 representing the percentage of animations to apply transformations on.

In [ ]:
project_path = "E:\Documents\Projects\Python\PycharmCurrent"
dataset_dir = "E:\Documents\Projects\Python\PycharmCurrent\Dataset"

flag_mirror = True # loads the mirrored animations
flag_transformations = False # random transformations
ratio_transformations = 0.1 # (max = 1)

##################################################################################################################################################################################################################

os.chdir(dataset_dir)

def fill_data_array(path):
    os.chdir(path)
    data_array = []
    for data_file in os.listdir():
        if data_file.endswith(".json"):
            if flag_mirror is False:
                if data_file[-13:-5] == "(Mirror)":
                    continue
            with open(data_file, 'r') as json_data:
                data = json.load(json_data) # returns JSON object as a dictionary
                data_array = data_array + data
    os.chdir(dataset_dir)
    return data_array

# Init data arrays
X_train = []
Y_train = []
x_test = []
y_test = []
x_val = []
y_val = []

sets = ["Train", "Test", "Validation"]
# Load input data (x)
for subset in sets:
    if subset == "Train":
        X_train = fill_data_array("Landmarks\\" + subset)
    elif subset == "Test":
        x_test = fill_data_array("Landmarks\\" + subset)
    elif subset == "Validation":
        x_val = fill_data_array("Landmarks\\" + subset)

# Load output data (y)
for subset in sets:
    if subset == "Train":
        Y_train = fill_data_array("Quaternions\\" + subset)
    elif subset == "Test":
        y_test = fill_data_array("Quaternions\\" + subset)
    elif subset == "Validation":
        y_val = fill_data_array("Quaternions\\" + subset)

# Shuffle the training data
x_train = []
y_train = []
index_shuffle = list(range(len(X_train))) # list of indices
random.shuffle(index_shuffle)
[x_train.append(X_train[idx]) for idx in index_shuffle]
[y_train.append(Y_train[idx]) for idx in index_shuffle]

if flag_transformations: # Only in training data
    aug_data_len = round(len(x_train) * ratio_transformations)
    aux_index = index_shuffle[:aug_data_len] # aux list of indices of data to apply data augmentation on
    for i in aux_index:
        ## Camera Movement in Z
        # get the data vector
        data_vec = X_train[i]
        dataGT_vec = Y_train[i]
        # map data to -1,1
        data_vec_norm = [(item * 2.0) - 1.0 for item in data_vec]
        # apply random factor between min and max zoom = [1.05, 1.72]
        scale = random.uniform(1.05, 1.73)
        data_vec_scaled = [item * scale for item in data_vec_norm]
        # return data to 0,1 (normalize again)
        aug_data = [(item + 1.0) / 2.0 for item in data_vec_scaled]
        # add the augmented data to the previous dataset
        x_train.append(aug_data)
        y_train.append(dataGT_vec)

        # Camera Movement in X and Y
        # add or subtract a little offset in x coordinate
        # - handle it as online preprocess step -

# Check data is something
if (len(x_train) != len(y_train)) or (len(x_test) != len(y_test)) or (len(x_val) != len(y_val)):
    print("ERROR: The length of the input data does not match the output data")
elif len(x_train) == 0 or len(y_train) == 0 or len(x_test) == 0 or len(y_test) == 0 or len(x_val) == 0 or len(y_val) == 0:
    print("ERROR: The length of some arrays is 0")
else:
    # Convert to tensors (GPU)
    #tf.debugging.set_log_device_placement(True) # print data location device
    x_train = tf.constant(x_train)
    y_train = tf.constant(y_train)
    x_test = tf.constant(x_test)
    y_test = tf.constant(y_test)
    x_val = tf.constant(x_val)
    y_val = tf.constant(y_val)

    print("Dataset Loaded Correctly")
    print("-> Total Data: " + str(len(x_train) + len(x_test) + len(x_val)))
    print("-> Split: Train - " + str(len(x_train)) + " // Test - " + str(len(x_test)) + " // Validation - " + str(len(x_val)))
    print("-> Input Length: " + str(len(x_train[0])) + " // Output Length: " + str(len(y_train[0])))

os.chdir(project_path)


### Class definition (must)

In [ ]:
def grouper(n, iterable, fillvalue=None):
    "grouper(3, 'ABCDEFG', 'x') --> ABC DEF Gxx"
    args = [iter(iterable)] * n
    return zip_longest(fillvalue=fillvalue, *args)

class SeqModel:
    def __init__(self, b_size, c_weights, opt='SGD', l_rate=0.01, i_layers=[1024]):
        self.batch_size = b_size
        self.custom_weights = c_weights
        if opt == 'SGD':
            self.optimizer = optimizers.SGD(learning_rate=l_rate)
        if opt == 'Adam':
            self.optimizer = optimizers.Adam(learning_rate=l_rate)
        if opt == 'Adamax':
            self.optimizer = optimizers.Adamax(learning_rate=l_rate)
        self.learning_rate = l_rate
        self.inner_layers = i_layers
        self.model = self.create()

    def create(self):
        def custom_loss_wrapper( weights ):
            def loss( y_true, y_pred ):
                sum_weights = tf.reduce_sum(weights) * tf.cast(tf.shape(y_pred)[0], dtype=tf.float32)
                resid = tf.reduce_sum(weights * tf.square(y_true - y_pred))
                return resid/sum_weights
            return loss

        model = Sequential()
        model.add(layers.LayerNormalization(input_dim=len(x_train[0])))
        for i in range(len(self.inner_layers)):
            model.add(layers.Dense(self.inner_layers[i], activation="relu", name="layer"+str(i)))
        model.add(layers.Dense(len(y_train[0]), activation='linear', name="layer_out"))
        model.compile(loss=custom_loss_wrapper(self.custom_weights), optimizer=self.optimizer, metrics=['accuracy'])

        return model

    def plot(self):
        self.model.summary()

    def train(self, epochs):
        history = self.model.fit(x_train, y_train,
                    batch_size=self.batch_size,
                    epochs=epochs,
                    validation_data=(x_val, y_val),
                    verbose=1,
                    #callbacks=callbacks_list
                )
        return history

    def predict(self, input_data, postpo=True):
        def normaliseQuats(data):
            for idx_frame, i in enumerate(data):
                for idx_quat, (x, y, z, w) in enumerate((grouper(4, i))):
                    sum = np.sqrt(x * x + y * y + z * z + w * w)
                    x /= sum
                    y /= sum
                    z /= sum
                    w /= sum
                    data[idx_frame][(idx_quat * 4):((idx_quat * 4) + 4)] = [x, y, z, w]
            return data

        output_data = self.model.predict(input_data, batch_size=self.batch_size)
        output_data = normaliseQuats(output_data) # Normalize the predicted quaternion

        if postpo:
            # Init postpo array
            output_data_pp = [[] for x in range(len(output_data))]
            # Apply a smooth filter to correct noise
            for i in range(len(output_data[0])):
                pp_data = savgol_filter([j[i] for j in output_data], 31, 3)  # https://scipy.github.io/old-wiki/pages/Cookbook/SavitzkyGolay
                [t.append(pp_data[idx]) for (idx, t) in enumerate(output_data_pp)]
            # Normalise again the quaternions
            return [output_data, normaliseQuats(output_data_pp)]
        else:
            return [output_data, None]

    def evaluate(self):
        tr_mse = self.model.evaluate(x_train, y_train, verbose=0)
        v_mse = self.model.evaluate(x_val, y_val, verbose=0)
        te_mse = self.model.evaluate(x_test, y_test, verbose=0)
        return [tr_mse, v_mse, te_mse]

    def save(self, path):
        # Save the model
        self.model.save(path)

        # Save the model serialized to JSON
        tfjs.converters.save_keras_model(self.model, os.path.join(path, "TensorflowJS_model"))
        model_json = self.model.to_json()
        with open(os.path.join(path, "TensorflowJS_model", "auxiliary_model.json"), "w") as json_file:
            json_file.write(model_json)

        # save configuration of the model
        with open(os.path.join(path, 'Model Configuration.txt'), 'w') as f:
            f.write('Test Loss: %.5f' % self.model.evaluate(x_test, y_test, verbose=0)[0] + '    Epochs: ' + str(n_epochs) + '    Batch Size: ' + str(self.batch_size) + '    Optimitzer: ' + self.optimizer._name + '    Learning Rate: ' + str(self.learning_rate) + '    Inner Layers: ' + str(self.inner_layers) + '    Custom Weights: ' + str(self.custom_weights))



### Models creation
**Create a model by using the code below. The inputs of the SeqModel() are the batch size (b_size), the custom weights for the Weighted Mean Square Error loss function (c_weights), the optimizer (opt) between ['SGD', 'Adam', 'Adamax'], the learning rate (l_rate), and the list of inner layers with their amount of weights (i_layers). See the previous cell for more information.**
> model = SeqModel()
> models.append(model)

Help: (https://www.tensorflow.org/tutorials/keras/regression)

In [ ]:
models = [] # list of models

# decay_lr_rate = optimizers.schedules.ExponentialDecay(
#      initial_learning_rate=0.02,
#      decay_steps=100000,
#      decay_rate=0.97)

quat_weights = tf.constant([ 0.1,0.1,0.1,1.0, 0.1,0.1,0.1,1.0, 0.1,0.1,0.1,1.0, 0.1,0.1,0.1,1.0,    # Hips, Spine, Spine1, Spine2
                                0.1,0.1,0.1,0.5, 0.1,0.1,0.1,0.5,                                       # Neck, Head
                                0.5,0.5,0.5,1.0, 0.5,0.5,0.5,1.0, 0.5,0.5,0.5,1.0, 0.5,0.5,0.5,1.0,     # (Left) Shoulder, Arm, Forearm, Hand
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Left) Thumb1, Thumb2, Thumb3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Left) Index1, Index2, Index3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Left) Middle1, Middle2, Middle3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Left) Ring1, Ring2, Ring3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Left) Pinky1, Pinky2, Pinky3
                                0.5,0.5,0.5,1.0, 0.5,0.5,0.5,1.0, 0.5,0.5,0.5,1.0, 0.5,0.5,0.5,1.0,     # (Right) Shoulder, Arm, Forearm, Hand
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Right) Thumb1, Thumb2, Thumb3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Right) Index1, Index2, Index3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Right) Middle1, Middle2, Middle3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Right) Ring1, Ring2, Ring3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0 ])                   # (Right) Pinky1, Pinky2, Pinky3

model = SeqModel(b_size=32, c_weights=quat_weights, opt='SGD', l_rate=0.01, i_layers=[1024, 1024])
model.plot()
models.append(model)

quat_weights = tf.constant([ 0.5,0.5,0.5,1.0, 0.5,0.5,0.5,1.0, 0.5,0.5,0.5,1.0, 0.5,0.5,0.5,1.0,    # Hips, Spine, Spine1, Spine2
                                0.1,0.1,0.1,0.1, 0.1,0.1,0.1,0.1,                                       # Neck, Head
                                1.0,1.0,1.0,1.0, 1.0,1.0,1.0,1.0, 1.0,1.0,1.0,1.0, 1.0,1.0,1.0,1.0,     # (Left) Shoulder, Arm, Forearm, Hand
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Left) Thumb1, Thumb2, Thumb3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Left) Index1, Index2, Index3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Left) Middle1, Middle2, Middle3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Left) Ring1, Ring2, Ring3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Left) Pinky1, Pinky2, Pinky3
                                1.0,1.0,1.0,1.0, 1.0,1.0,1.0,1.0, 1.0,1.0,1.0,1.0, 1.0,1.0,1.0,1.0,     # (Right) Shoulder, Arm, Forearm, Hand
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Right) Thumb1, Thumb2, Thumb3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Right) Index1, Index2, Index3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Right) Middle1, Middle2, Middle3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0,                     # (Right) Ring1, Ring2, Ring3
                                     0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0, 0.2,0.2,0.2,1.0 ])                   # (Right) Pinky1, Pinky2, Pinky3

model = SeqModel(b_size=16, c_weights=quat_weights, opt='SGD', l_rate=0.01, i_layers=[1024, 1024])
models.append(model)

model = SeqModel(b_size=8, c_weights=quat_weights, opt='SGD', l_rate=0.01, i_layers=[1024, 1024])
models.append(model)


### Training loop
**n_epochs:** Set the number of epochs of your training process.

In [ ]:
n_epochs = 200

##################################################################################################################################################################################################################

histories = []
for (i, m) in enumerate(models):
    h = m.train(epochs=n_epochs)
    histories.append(h)
    print('\n### Model [' + str(i+1) + '] ### Trained without error\n')


### Loss Evaluation
It plots the losses of all the models and save the plot as "Loss.pdf". No actions needed by user.

In [ ]:
path_losses = project_path + "\Losses"
os.makedirs(path_losses, exist_ok=True)
os.chdir(path_losses)

# Automatically compute next id
save_path = ""
try:
    last_saved_loss = sorted(os.listdir())[-1]
    next_idx = int(last_saved_loss[-2:]) + 1
    if next_idx < 10:
        save_path = os.path.join("Loss_0" + str(next_idx))
    else:
        save_path = os.path.join("Loss_" + str(next_idx))
except:
    save_path = "Loss_01"
os.makedirs(os.path.join(path_losses, save_path), exist_ok=True)

# save info of the plot
with open(os.path.join(path_losses, save_path, 'PlotInfo.txt'), 'w') as f:
    f.write('Epochs: ' + str(n_epochs)+ '\n\n')
    for (i, m) in enumerate(models):
        [train_mse, val_mse, test_mse] = m.evaluate()
        print('## Model ' + str(i+1) + ' ##   Train Data Loss: %.5f' % train_mse[0] + '     Validation Data Loss: %.5f' % val_mse[0] + '     Test Data Loss: %.5f' % test_mse[0])
        #'    Accuracy: %.2f' % (train_mse[1]*100)
        f.write('>> Model ' + str(i+1) + ': batch_size=' + str(m.batch_size) + '    optimitzer=' + str(m.optimizer._name) + '    learning_rate=' + str(m.learning_rate) + '  inner_layers=' + str(m.inner_layers) + '    train_loss: %.5f' % train_mse[0] + '     validation_loss: %.5f' % val_mse[0] + '     test_loss: %.5f' % test_mse[0] + '\n')

# Plots
fig = plt.figure(figsize=(15, 5))
ax1 = fig.add_subplot(111)
ax1.title.set_text('Model Loss')
ax1.set_ylabel('Loss')
ax1.set_xlabel('Epoch')

colors = ['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd', '#bcbd22'] # list of colors for the lines in plot
for (i, h) in enumerate(histories):
    c = colors[i]
    # Summarize history for loss
    ax1.plot(h.history['loss'], color=c, label='model '+str(i))
    ax1.plot(h.history['val_loss'], '--', color=c, label='_nolegend_')

plt.ylim([0, 0.0125])
plt.locator_params(axis='x', nbins=8)
plt.legend(loc='upper right')
plt.show()

name = os.path.join(path_losses, save_path, 'Loss.pdf')
fig.savefig(name , bbox_inches='tight')
plt.close()

print('INFO:Loss stored in folder: "' + save_path + '"')

# Accuracy plot
#ax2 = fig.add_subplot(122)
# ax2.plot(h.history['accuracy'])
# ax2.plot(h.history['val_accuracy'])
# ax2.title.set_text('model accuracy')
# ax2.set_ylabel('accuracy')
# ax2.set_xlabel('epoch')
# ax2.legend(['train', 'validation'], loc='upper left')


### Save the Model
**model2save:** Choose the model from the list of models that you want to save in case you have created/trained multiples. If you don't modify this, it will save the first created model (models[0]).

In [ ]:
model2save = models[0]

##################################################################################################################################################################################################################

os.makedirs(project_path + "\Models", exist_ok=True)
os.chdir(project_path + "\Models")

# Automatically compute next id
save_path = ""
try:
    last_saved_model = sorted(os.listdir())[-1]
    next_idx = int(last_saved_model[-2:]) + 1
    if next_idx < 10:
        save_path = os.path.join("saved_model_0" + str(next_idx))
    else:
        save_path = os.path.join("saved_model_" + str(next_idx))
except:
    save_path = "saved_model_01"

# Save the model
model2save.save(save_path)

os.chdir("../")

### Load the Model
**model2load:** Set the number of the model you want to load. Add "1" if you want to load the model from the folder "saved_model_1".

In [ ]:
model2load = "10" # indicate the id of the model to load (check the list in \Models)

##################################################################################################################################################################################################################

model = load_model(project_path + "\Models\saved_model_" + model2load, compile=False) # compile=False means that we cannot train more
models.append(model) # it will be included in the list of models


### Prediction test
**model2predict:** Choose the model from the list of models that you want to save in case you have created/trained multiples. If you don’t modify this, it will use the first created model (models[0]) to do the predictions.
**flag_plot:** Flag to create error plots. Setting it to False reduces its computation time.
**flag_postpo:** Set to False for skipping the smooth filer. True gives much better results.

In [ ]:
model2predict = models[0]  # choose model in case we have several trained
flag_plot = False # flag to create error plots. Setting it to False reduces its computation time
flag_postpo = True  # set to False for skipping the smooth filer. True gives much better results

##################################################################################################################################################################################################################

# From https://automaticaddison.com/how-to-convert-a-quaternion-into-euler-angles-in-python/
def euler_from_quaternion(x, y, z, w):
    """
    Convert a quaternion into euler angles (roll, pitch, yaw)
    roll is rotation around x in radians (counterclockwise)
    pitch is rotation around y in radians (counterclockwise)
    yaw is rotation around z in radians (counterclockwise)
    """
    t0 = +2.0 * (w * x + y * z)
    t1 = +1.0 - 2.0 * (x * x + y * y)
    roll_x = math.atan2(t0, t1)

    t2 = +2.0 * (w * y - z * x)
    t2 = +1.0 if t2 > +1.0 else t2
    t2 = -1.0 if t2 < -1.0 else t2
    pitch_y = math.asin(t2)

    t3 = +2.0 * (w * z + x * y)
    t4 = +1.0 - 2.0 * (y * y + z * z)
    yaw_z = math.atan2(t3, t4)

    return roll_x, pitch_y, yaw_z  # in radians

list_quats = [
        "Hips",
        "Spine",
        "Spine1",
        "Spine2",
        "Neck",
        "Head",
        "LeftShoulder",
        "LeftArm",
        "LeftForeArm",
        "LeftHand",
        "LeftHandThumb1",
        "LeftHandThumb2",
        "LeftHandThumb3",
        "LeftHandIndex1",
        "LeftHandIndex2",
        "LeftHandIndex3",
        "LeftHandMiddle1",
        "LeftHandMiddle2",
        "LeftHandMiddle3",
        "LeftHandRing1",
        "LeftHandRing2",
        "LeftHandRing3",
        "LeftHandPinky1",
        "LeftHandPinky2",
        "LeftHandPinky3",
        "RightShoulder",
        "RightArm",
        "RightForeArm",
        "RightHand",
        "RightHandThumb1",
        "RightHandThumb2",
        "RightHandThumb3",
        "RightHandIndex1",
        "RightHandIndex2",
        "RightHandIndex3",
        "RightHandMiddle1",
        "RightHandMiddle2",
        "RightHandMiddle3",
        "RightHandRing1",
        "RightHandRing2",
        "RightHandRing3",
        "RightHandPinky1",
        "RightHandPinky2",
        "RightHandPinky3",
    ]  # List of all the bones that have quaternions
os.chdir(os.path.join(dataset_dir, "Landmarks\Test"))

for file in os.listdir():
    if file.endswith(".json"):
        # load the data
        with open(file, 'r') as f:
            data_in_test = json.load(f)
        with open(os.path.join("../../Quaternions/Test", file), 'r') as f:
            data_out_test = json.load(f)

        # PREDICTION
        [data_pred, data_pred_postpo] = model2predict.predict(data_in_test, postpo=flag_postpo)

        # Save the predicted values
        file_path = os.path.join(project_path, "Predictions", file[:-5])
        os.makedirs(file_path, exist_ok=True)
        with open(os.path.join(file_path, file[:-5] + "_Prediction.json"), 'w') as f:
            json.dump(np.array(data_pred_postpo).tolist(), f, indent=4)

        # Compute the Error of the Quaternions in (Roll, Pitch, Yaw)
        count = 0
        n = int(len(data_out_test[0]) / 4)
        eval_angles = [[] for x in range(n)]  # list of the error angles per bone at all frames
        for (frame, frame_gt) in zip(data_pred_postpo, data_out_test):
            frame_angles = []  # init
            for (x, y, z, w), (X, Y, Z, W) in zip(grouper(4, frame), grouper(4, frame_gt)):
                roll, pitch, yaw = euler_from_quaternion(x, y, z, w)
                roll_gt, pitch_gt, yaw_gt = euler_from_quaternion(X, Y, Z, W)
                # compare with GT
                # we don't check cases like 360 vs 0 because it would increase the computational time, and it is never the case
                # if the error of angles exceeds 180 degrees maybe we should implement it
                roll_err = abs(np.rad2deg(roll - roll_gt))
                pitch_err = abs(np.rad2deg(pitch - pitch_gt))
                yaw_err = abs(np.rad2deg(yaw - yaw_gt))
                # add to the lists
                eval_angles[count].append([roll_err, pitch_err, yaw_err])
                count += 1
            count = 0  # reset bone idx
        with open(os.path.join(file_path, "EvaluationAngles.json"), 'w') as f:
            json.dump(eval_angles, f, indent=4)

        # Plot the results
        if flag_plot:
            for b_idx in range(int(len(data_pred[0]) / 4)):  # 176 / 4 = 44 is the number of joints in the array of quaternions
                f = plt.figure(figsize=(20, 10))
                xx1 = f.add_subplot(221)
                xx2 = f.add_subplot(222)
                xx3 = f.add_subplot(223)
                xx4 = f.add_subplot(224)

                subplot_set = [xx1, xx2, xx3, xx4]
                subplot_axis = ["X", "Y", "Z", "W"]
                subplot_colors = [['#13476c', '#79add2'], ['#b3590a', '#ffb26e'], ['#1f701f', '#96d096'], ['#593e71', '#a985ca']] # for X,Y,Z,W respectively

                for i, xxi in enumerate(subplot_set):
                    xxi.plot([j[b_idx * 4 + i] for j in data_out_test], color=subplot_colors[i][0])  # GT data
                    xxi.plot([j[b_idx * 4 + i] for j in data_pred], color=subplot_colors[i][1])  # Pred data
                    xxi.plot([j[b_idx * 4 + i] for j in data_pred_postpo], color='red')  # Post-processed pred data

                    xxi.title.set_text(subplot_axis[i] + " Component")
                    xxi.set_xlabel("Frames")
                    xxi.legend([subplot_axis[i] + " (GT)", subplot_axis[i] + " (Pred)",  "Final Estimation"], loc="upper left")

                f.savefig(os.path.join(file_path, file[:-5] + "_" + list_quats[b_idx] + '.pdf'), bbox_inches='tight')
                plt.close()

        print("INFO:Prediction of the animation <" + file[:-5] + "> done correctly.")


### Evaluation of the predictions
**animation2evaluate:** Name of the animation to evaluate. Indicate the name as it is spelled in the folder inside "\Predictions".

In [ ]:
animation2evaluate = "Back Squat"

##################################################################################################################################################################################################################

bone_list = [
    "mixamorigHips",
    "mixamorigSpine",
    "mixamorigSpine1",
    "mixamorigSpine2",
    "mixamorigNeck",
    "mixamorigHead",
    "mixamorigHead_Top",
    "ENDSITE",
    "mixamorigLeftShoulder",
    "mixamorigLeftArm",
    "mixamorigLeftForeArm",
    "mixamorigLeftHand",
    "mixamorigLeftHandThumb1",
    "mixamorigLeftHandThumb2",
    "mixamorigLeftHandThumb3",
    "mixamorigLeftHandThumb4",
    "ENDSITE",
    "mixamorigLeftHandIndex1",
    "mixamorigLeftHandIndex2",
    "mixamorigLeftHandIndex3",
    "mixamorigLeftHandIndex4",
    "ENDSITE",
    "mixamorigLeftHandMiddle1",
    "mixamorigLeftHandMiddle2",
    "mixamorigLeftHandMiddle3",
    "mixamorigLeftHandMiddle4",
    "ENDSITE",
    "mixamorigLeftHandRing1",
    "mixamorigLeftHandRing2",
    "mixamorigLeftHandRing3",
    "mixamorigLeftHandRing4",
    "ENDSITE",
    "mixamorigLeftHandPinky1",
    "mixamorigLeftHandPinky2",
    "mixamorigLeftHandPinky3",
    "mixamorigLeftHandPinky4",
    "ENDSITE",
    "mixamorigRightShoulder",
    "mixamorigRightArm",
    "mixamorigRightForeArm",
    "mixamorigRightHand",
    "mixamorigRightHandThumb1",
    "mixamorigRightHandThumb2",
    "mixamorigRightHandThumb3",
    "mixamorigRightHandThumb4",
    "ENDSITE",
    "mixamorigRightHandIndex1",
    "mixamorigRightHandIndex2",
    "mixamorigRightHandIndex3",
    "mixamorigRightHandIndex4",
    "ENDSITE",
    "mixamorigRightHandMiddle1",
    "mixamorigRightHandMiddle2",
    "mixamorigRightHandMiddle3",
    "mixamorigRightHandMiddle4",
    "ENDSITE",
    "mixamorigRightHandRing1",
    "mixamorigRightHandRing2",
    "mixamorigRightHandRing3",
    "mixamorigRightHandRing4",
    "ENDSITE",
    "mixamorigRightHandPinky1",
    "mixamorigRightHandPinky2",
    "mixamorigRightHandPinky3",
    "mixamorigRightHandPinky4",
    "ENDSITE",
    "mixamorigLeftUpLeg",
    "mixamorigLeftLeg",
    "mixamorigLeftFoot",
    "mixamorigLeftToeBase",
    "mixamorigLeftToe_End",
    "ENDSITE",
    "mixamorigRightUpLeg",
    "mixamorigRightLeg",
    "mixamorigRightFoot",
    "mixamorigRightToeBase",
    "mixamorigRightToe_End",
    "ENDSITE"
] # List of all the bones
bone_list_quats = [
    "mixamorigHips",
    "mixamorigSpine",
    "mixamorigSpine1",
    "mixamorigSpine2",
    "mixamorigNeck",
    "mixamorigHead",
    "mixamorigLeftShoulder",
    "mixamorigLeftArm",
    "mixamorigLeftForeArm",
    "mixamorigLeftHand",
    "mixamorigLeftHandThumb1",
    "mixamorigLeftHandThumb2",
    "mixamorigLeftHandThumb3",
    "mixamorigLeftHandIndex1",
    "mixamorigLeftHandIndex2",
    "mixamorigLeftHandIndex3",
    "mixamorigLeftHandMiddle1",
    "mixamorigLeftHandMiddle2",
    "mixamorigLeftHandMiddle3",
    "mixamorigLeftHandRing1",
    "mixamorigLeftHandRing2",
    "mixamorigLeftHandRing3",
    "mixamorigLeftHandPinky1",
    "mixamorigLeftHandPinky2",
    "mixamorigLeftHandPinky3",
    "mixamorigRightShoulder",
    "mixamorigRightArm",
    "mixamorigRightForeArm",
    "mixamorigRightHand",
    "mixamorigRightHandThumb1",
    "mixamorigRightHandThumb2",
    "mixamorigRightHandThumb3",
    "mixamorigRightHandIndex1",
    "mixamorigRightHandIndex2",
    "mixamorigRightHandIndex3",
    "mixamorigRightHandMiddle1",
    "mixamorigRightHandMiddle2",
    "mixamorigRightHandMiddle3",
    "mixamorigRightHandRing1",
    "mixamorigRightHandRing2",
    "mixamorigRightHandRing3",
    "mixamorigRightHandPinky1",
    "mixamorigRightHandPinky2",
    "mixamorigRightHandPinky3",
] # List of all the bones that have quaternions

eval_data_path = os.path.join(project_path, "Predictions", animation2evaluate)
os.chdir(eval_data_path)

# Load the data
try:
    with open(os.path.join(eval_data_path, "EvaluationDistances.json"), "r") as f:
        eval_dist = json.load(f)
    with open(os.path.join(eval_data_path, "EvaluationPositions.json"), "r") as f:
        eval_pos = json.load(f)
    with open(os.path.join(eval_data_path, "EvaluationAngles.json"), "r") as f:
        eval_ang = json.load(f)
except:
    print('ERROR:Evaluation of the animation <' + animation2evaluate + '> cannot be done. Get required "EvaluationDistances.json" and "EvaluationPositions.json" files by evaluating the animations in the following online animations view tool: https://github.com/victorubieto/animationLoader')
    assert False

for bone in bone_list_quats:
    # Find the index with respect to the selected bone to evaluate
    idx = bone_list.index(bone)
    idx2 = bone_list_quats.index(bone)
    b_to_evaluate = bone[9:] # remove "mixamorig" tag
    bone_positions = eval_pos[idx]
    bone_angles = eval_ang[idx2]

    ### Positions error
    fig_pos = plt.figure(figsize=(20, 5))
    bx = fig_pos.add_subplot(131)
    by = fig_pos.add_subplot(132)
    bz = fig_pos.add_subplot(133)
    subplot_set = [bx, by, bz]
    subplot_axis = ["X", "Y", "Z"]
    for i, bi in enumerate(subplot_set):
        bi.plot(bone_positions[0][i])
        bi.plot(bone_positions[1][i])
        bi.locator_params(nbins=4)
        bi.title.set_text(b_to_evaluate + " - " + subplot_axis[i] + " axis")
        bi.set_ylabel("Centimeters")
        bi.set_xlabel("Frames")
        bi.legend(["Ground Truth", "Prediction"], loc="upper left")
    fig_pos.savefig(os.path.join(file, b_to_evaluate + "_Positions.pdf"), bbox_inches='tight')
    plt.close()

    ### Distance error
    fig_dist = plt.figure(figsize=(20, 5))
    dx = fig_dist.add_subplot(1,1,1)
    dx.plot(eval_dist[idx])
    dx.title.set_text("Error distance between ground truth and prediction <" + b_to_evaluate + "> joint")
    dx.set_ylabel("Centimeters")
    dx.set_xlabel("Frames")
    sum_err = np.sum(eval_dist[idx])
    print(file + " <" + b_to_evaluate + "> MIN err dist %.3f " % min(eval_dist[idx]) + "cm  || MAX err dist %.3f " % max(eval_dist[idx]) +
          "cm  || MEAN err dist %.3f " % (sum_err/len(eval_dist[idx])) + "cm  || TOTAL err dist %.3f " % sum_err + "cm")
    fig_dist.savefig(os.path.join(file, b_to_evaluate + "_Distances.pdf"), bbox_inches='tight')
    plt.close()

    ### Angle error
    fig_ang = plt.figure(figsize=(20, 5))
    ax = fig_ang.add_subplot(1,1,1)
    ax.plot([item[0] for item in bone_angles])
    ax.plot([item[1] for item in bone_angles])
    ax.plot([item[2] for item in bone_angles])
    ax.title.set_text("Error angle between ground truth and prediction <" + b_to_evaluate + "> joint")
    ax.set_ylabel("Degrees")
    ax.set_xlabel("Frames")
    ax.legend(["yaw", "pitch", "roll"], loc="upper left")
    fig_ang.savefig(os.path.join(file, b_to_evaluate + "_Angles.pdf"), bbox_inches='tight')
    plt.close()


### (Run only once) Divide the data in train/val/test. Use the same division for training experiments for consistency
This cell uses the "dataset_dir" variable from the cells above to find the dataset folder.

In [ ]:
# We want always tha same division, it makes the evaluation easier
def split_data(folder_path, train_size, test_size, val_size):
    prev_dir = os.getcwd() # get previous dir
    os.chdir(folder_path) # go to the folder dir

    # get length of files in folder
    file_paths = os.listdir()
    [file_paths.remove(f) for f in file_paths if ".json" not in f] # remove unnecessary files (gt folder)
    data_len = len(file_paths)

    # compute the percentages
    tr_size = round(data_len * train_size)
    te_size = round(data_len * test_size)
    v_size = data_len - tr_size - te_size

    random.shuffle(file_paths) # shuffle the list of files

    # loop of copying files into directory train
    os.makedirs("Train", exist_ok=True)
    os.makedirs("Test", exist_ok=True)
    os.makedirs("Validation", exist_ok=True)
    os.makedirs("Train\gt", exist_ok=True)
    os.makedirs("Test\gt", exist_ok=True)
    os.makedirs("Validation\gt", exist_ok=True)

    for (idx, f) in enumerate(file_paths):
        if idx < tr_size:
            shutil.copy(f, os.path.join("Train", f))
            shutil.copy(os.path.join("gt", f), os.path.join("Train\gt", f))
        elif idx < (tr_size + te_size):
            shutil.copy(f, os.path.join("Test", f))
            shutil.copy(os.path.join("gt", f), os.path.join("Test\gt", f))
        else:
            shutil.copy(f, os.path.join("Validation", f))
            shutil.copy(os.path.join("gt", f), os.path.join("Validation\gt", f))
    os.chdir(prev_dir) # return to initial dir

split_data(dataset_dir, train_size=0.7, test_size=0.1, val_size=0.2)
print("Application Message: Dataset split without any problem")